# Run various tests on models

In [1]:
from game.game import Game
from game.data.generator import create_numbers
import torch
import os

In [2]:
# loads checkpoint and does one epoch, shows acc on validation set
def load(last_save, model_size, model_number, run_number, vocab, sender, receiver, embedding, length=1):
    epochs = last_save + 1
    save_name = "game/models/game{}_{}_{}_{}_{}_{}_{}".format(model_size, model_number, run_number, vocab, sender, receiver, embedding)
    if(length > 1):
        save_name = "{}_{}".format(save_name, length)
    

    params = [
        '--batch_size=1',
        '--n_epochs={}'.format(epochs),
        '--vocab_size={}'.format(vocab),
        '--sender_hidden={}'.format(sender),
        '--receiver_hidden={}'.format(receiver),
        '--lr=0.001',
        '--max_len={}'.format(length),
        '--sender_entropy=0.5',
        '--sender_embedding={}'.format(embedding),
        '--receiver_embedding={}'.format(embedding),
        '--validation_freq=10',
        '--train_data=game/data/train10.txt',
        '--validation_data=game/data/validation10.txt',
        '--load_from_checkpoint={}_{}.tar'.format(save_name, last_save)
    ]
    game = Game(params)
    game.play()
    return game

In [3]:
def predict_and_print(model, inputs, labels):
    inputs_tensor = torch.FloatTensor(inputs)
    labels_tensor = torch.FloatTensor(labels)
    prediction = model.game.forward(inputs_tensor,labels_tensor)
    messages = prediction[1].message.tolist()
    outputs = prediction[1].receiver_output.tolist()
    for q in range(len(outputs)):
        print("{} {} {} {}".format(inputs[q], messages[q], outputs[q], labels[q]))
    unique_outputs = set([item[0] for item in outputs])
    number_unique = len(unique_outputs)
    acc = prediction[1].aux['acc'].mean().item()
    print("Unique outputs: {}: {}".format(number_unique, unique_outputs))
    print("Accuracy: {}".format(acc))
    return acc, number_unique, outputs


In [4]:
extra_tests = {}
def test_above_limit(game, start, end, number_of_samples):
    # creates more samples for model to predict
    inputs, labels = extra_tests.get((start, end, number_of_samples), (None, None))
    if(inputs is None or labels is None):
        inputs, labels = create_numbers(end, number_of_samples, False, False, start)
        extra_tests[(start, end, number_of_samples)] = (inputs, labels)
        print("Inputs: {}".format(inputs))
        print("Labels: {}".format(labels))
    print("Testing {} samples of numbers that sum up to [{} - {}]".format(number_of_samples, start, end))
    return predict_and_print(game, inputs, labels)

In [5]:
def test_all_set(game, n):
    inputs = []
    labels = []
    for i in range(n+1):
        for j in range(n+1):
            if i+j <= n:
                inputs.append([i, j])
                labels.append([i+j]) 
    print("Testing {} samples of numbers that sum up to {}".format(len(inputs), n))
    return predict_and_print(game, inputs, labels)

In [6]:
def test_validation_only(game):
    frame = game.trainer.validation_data.dataset.frame
    inputs = [f[0].tolist() for f in frame]
    labels = [f[1].tolist() for f in frame]
    return predict_and_print(game, inputs, labels)

In [7]:
def test_some_other_numbers(game):
    inputs = [[9.0, 0.2], [0., 0.3],[6.0, 4.0],[6.0, 4.0],[9.0, 1.0],[9.0, 1.0],[9.0, 1.0],[1.0, 1.0],[1.0, 1.0],[1.0, 1.0], [0.0, 1.0], [0.0, 0.0], [-1.0, 4.0], [5.0, -2.0], [-1.0, 0.0], [-2.0, -2.0], [-9.0, -1.0], [8.0, -3.0], [-10.0, -10.0]]
    labels = [[9.2],[.3],[10.],[10.],[10.],[10.],[10.],[2.0],[2.0],[2.0],[1.0],[0.0],[3.0],[3.0], [-1.0], [-4.0], [-10.0], [5.0], [-20.0]]
    return predict_and_print(game, inputs, labels)

In [8]:
def test_synonymy(game, n, repeat):
    limit = n+1
    accs_input = {}
    messages_input = {}
    accs_label = {}
    messages_label = {}
    for i in range(limit):
        for j in range(limit):
            if(i+j <= n):
                inputs = []
                labels = []
                for p in range(repeat):
                    inputs.append([i, j])
                    labels.append([i+j]) 
                
                a, m, o = predict_and_print(game, inputs, labels)
                
                input = (inputs[0][0],inputs[0][1])
                label = labels[0][0]
                accs_input[input] = a
                messages_input[input] = m
                
                l = messages_label.get(label, [])
                l.append(o)
                messages_label[label] = l
                
                l = accs_label.get(label, [])
                l.append(a)
                accs_label[label] = l
                
    for i in range(limit):
        outputs = [output[0] for outputs in messages_label[i] for output in outputs]
        messages_label[i] = len(set(outputs))
        accs_label[i] = sum(accs_label[i])/len(accs_label[i])
        
    print("Unique messages per input: {}".format(messages_input))
    print("Accuracies per input: {}".format(accs_input))
    return accs_label, messages_label, _

In [9]:
def test_various_ranges(game, start_numbers, end_numbers, n_samples):
    accs = []
    ns_symbols = []
    for i in range(len(start_numbers)):  
        acc, n_symbols, _ = test_above_limit(game, start_numbers[i], end_numbers[i], n_samples[i])
        accs.append(acc)
        ns_symbols.append(n_symbols)
    print("Accuracies: {}".format(accs))
    print("Number of messages: {}".format(ns_symbols))
    return accs, ns_symbols, _

In [10]:
def run_test(games, test):
    accs = []
    ns_symbols= []
    
    for i in range(len(games)):
        print("\n--------")
        print("Running test for game {}".format(i))
        acc, n_symbols, _ = test(games[i])
        accs.append(acc)
        ns_symbols.append(n_symbols)
        
    print("\n--------")
    print("All games:")
    for i in range(len(accs)):
        print("Game {},  Number of messages: {}, Accuracy: {}".format(i, ns_symbols[i], accs[i]))

In [25]:
games10 = [
    load(6000, 10, 14, 1, 16, 16, 16, 5),#game10_14_1_16_16_16_5_6000.tar
    load(1500, 10, 14, 1, 32, 32, 32, 7), #game10_14_1_32_32_32_7_1500.tar
    load(1500, 10, 14, 1, 32, 64, 32, 7), # game10_14_1_32_64_32_7_1500.tar
    load(1500, 10, 14, 1, 64, 64, 64, 7), #game10_14_1_64_64_64_7_1500.tar
    load(1500, 10, 14, 1, 64, 128, 64, 8), # game10_14_1_64_128_64_8_1500.tar
    load(3000, 10, 14, 3, 64, 64,64, 7),
    load(6000, 10, 14, 3, 64, 64,64, 7),
    load(1500, 10, 15, 1, 64, 64, 64, 7, 2), #game10_15_1_64_64_64_7_2_1500.tar
    load(1500, 10, 15, 2, 16, 16,16, 5, 2),
    load(6000, 10, 15, 1, 64, 64, 64, 7, 2),
    load(6000, 10, 15, 2, 16, 16,16, 5, 2),
]

Preparing dataset...
Samples in training set: 52
Samples in test set: 14

----------
Building model...
# Initializing model, trainer, and optimizer from game/models/game10_14_1_16_16_16_5_6000.tar
# loading trainer state from game/models/game10_14_1_16_16_16_5_6000.tar
SenderReceiverRnnReinforce(
  (sender): RnnSenderReinforce(
    (agent): LayerWrapper(
      (output): Linear(in_features=2, out_features=16, bias=True)
    )
    (hidden_to_output): Linear(in_features=16, out_features=16, bias=True)
    (embedding): Embedding(16, 5)
    (cells): ModuleList(
      (0): RNNCell(5, 16)
    )
  )
  (receiver): RnnReceiverDeterministic(
    (agent): LayerWrapper(
      (output): Linear(in_features=16, out_features=1, bias=True)
    )
    (encoder): RnnEncoder(
      (cell): RNN(5, 16, batch_first=True)
      (embedding): Embedding(16, 5)
    )
  )
  (mechanics): CommunicationRnnReinforce()
)
Number of parameters 1238

----------
Start of training... 2021-11-11 16:10:57.886379
{"loss": -0.155

{"loss": -0.6801649928092957, "acc": 0.9038461446762085, "sender_entropy": 0.9824610948562622, "receiver_entropy": 0.0, "length": 2.0, "mode": "train", "epoch": 6001}
End of training... 2021-11-11 16:10:59.593958
Duration: 0.22 seconds
Preparing dataset...
Samples in training set: 52
Samples in test set: 14

----------
Building model...
# Initializing model, trainer, and optimizer from game/models/game10_15_1_64_64_64_7_2_1500.tar
# loading trainer state from game/models/game10_15_1_64_64_64_7_2_1500.tar
SenderReceiverRnnReinforce(
  (sender): RnnSenderReinforce(
    (agent): LayerWrapper(
      (output): Linear(in_features=2, out_features=64, bias=True)
    )
    (hidden_to_output): Linear(in_features=64, out_features=64, bias=True)
    (embedding): Embedding(64, 7)
    (cells): ModuleList(
      (0): RNNCell(7, 64)
    )
  )
  (receiver): RnnReceiverDeterministic(
    (agent): LayerWrapper(
      (output): Linear(in_features=64, out_features=1, bias=True)
    )
    (encoder): RnnEnco

# Test whole number range

In [26]:
run_test(games10, lambda x: test_all_set(x, 10))


--------
Running test for game 0
Testing 66 samples of numbers that sum up to 10
[0, 0] [12, 0] [0.6291986703872681] [0]
[0, 1] [0, 0] [0.7613338232040405] [1]
[0, 2] [2, 0] [2.596240520477295] [2]
[0, 3] [2, 0] [2.596240520477295] [3]
[0, 4] [15, 0] [4.493517875671387] [4]
[0, 5] [15, 0] [4.493517875671387] [5]
[0, 6] [13, 0] [5.9797797203063965] [6]
[0, 7] [8, 0] [7.010116100311279] [7]
[0, 8] [9, 0] [9.469077110290527] [8]
[0, 9] [4, 0] [9.499030113220215] [9]
[0, 10] [4, 0] [9.499030113220215] [10]
[1, 0] [0, 0] [0.7613338232040405] [1]
[1, 1] [2, 0] [2.596240520477295] [2]
[1, 2] [2, 0] [2.596240520477295] [3]
[1, 3] [15, 0] [4.493517875671387] [4]
[1, 4] [15, 0] [4.493517875671387] [5]
[1, 5] [13, 0] [5.9797797203063965] [6]
[1, 6] [8, 0] [7.010116100311279] [7]
[1, 7] [6, 0] [7.990846157073975] [8]
[1, 8] [11, 0] [9.48570728302002] [9]
[1, 9] [11, 0] [9.48570728302002] [10]
[2, 0] [2, 0] [2.596240520477295] [2]
[2, 1] [2, 0] [2.596240520477295] [3]
[2, 2] [15, 0] [4.49351787567

# Test validation only

In [27]:
run_test(games10, lambda x: test_validation_only(x))


--------
Running test for game 0
[5.0, 3.0] [5, 0] [7.996931552886963] [8.0]
[5.0, 2.0] [8, 0] [7.010116100311279] [7.0]
[0.0, 10.0] [7, 0] [9.499651908874512] [10.0]
[7.0, 0.0] [8, 0] [7.010116100311279] [7.0]
[5.0, 0.0] [15, 0] [4.493517875671387] [5.0]
[4.0, 0.0] [15, 0] [4.493517875671387] [4.0]
[0.0, 5.0] [15, 0] [4.493517875671387] [5.0]
[7.0, 3.0] [11, 0] [9.48570728302002] [10.0]
[1.0, 2.0] [2, 0] [2.596240520477295] [3.0]
[1.0, 8.0] [11, 0] [9.48570728302002] [9.0]
[2.0, 8.0] [4, 0] [9.499030113220215] [10.0]
[2.0, 0.0] [2, 0] [2.596240520477295] [2.0]
[4.0, 3.0] [8, 0] [7.010116100311279] [7.0]
[5.0, 1.0] [13, 0] [5.9797797203063965] [6.0]
Unique outputs: 8: {2.596240520477295, 4.493517875671387, 5.9797797203063965, 7.010116100311279, 7.996931552886963, 9.499651908874512, 9.48570728302002, 9.499030113220215}
Accuracy: 0.5714285969734192

--------
Running test for game 1
[5.0, 3.0] [19, 0] [7.974984169006348] [8.0]
[5.0, 2.0] [10, 0] [6.767304420471191] [7.0]
[0.0, 10.0] [7, 

# Test above number range

In [28]:
start_numbers = [11, 13, 50, 101]
end_numbers = [12, 20, 100, 100000]
n_samples = [10, 100, 100, 1000]
run_test(games10, lambda x: test_various_ranges(x, start_numbers, end_numbers, n_samples))


--------
Running test for game 0
Testing 10 samples of numbers that sum up to [11 - 12]
[4, 7] [9, 0] [9.469077110290527] [11]
[5, 6] [7, 0] [9.499651908874512] [11]
[2, 10] [3, 0] [9.498169898986816] [12]
[11, 1] [10, 0] [9.496932029724121] [12]
[1, 10] [4, 0] [9.499030113220215] [11]
[6, 5] [7, 0] [9.499651908874512] [11]
[8, 4] [14, 0] [9.496609687805176] [12]
[10, 1] [11, 0] [9.48570728302002] [11]
[7, 4] [7, 0] [9.499651908874512] [11]
[0, 11] [14, 0] [9.496609687805176] [11]
Unique outputs: 7: {9.469077110290527, 9.496932029724121, 9.499030113220215, 9.499651908874512, 9.498169898986816, 9.496609687805176, 9.48570728302002}
Accuracy: 0.0
Testing 100 samples of numbers that sum up to [13 - 20]
[12, 2] [10, 0] [9.496932029724121] [14]
[14, 0] [3, 0] [9.498169898986816] [14]
[0, 20] [3, 0] [9.498169898986816] [20]
[16, 3] [3, 0] [9.498169898986816] [19]
[2, 18] [11, 0] [9.48570728302002] [20]
[12, 7] [11, 0] [9.48570728302002] [19]
[12, 8] [4, 0] [9.499030113220215] [20]
[2, 13] [7

[32645, 2599] [20, 0] [10.35618782043457] [35244]
[53774, 30503] [30, 0] [9.78769302368164] [84277]
[72163, 14971] [20, 0] [10.35618782043457] [87134]
[33317, 1080] [20, 0] [10.35618782043457] [34397]
[1378, 10344] [12, 0] [10.416776657104492] [11722]
[34060, 49109] [20, 0] [10.35618782043457] [83169]
[41271, 13826] [12, 0] [10.416776657104492] [55097]
[6760, 3895] [12, 0] [10.416776657104492] [10655]
[5925, 29303] [20, 0] [10.35618782043457] [35228]
[13062, 7081] [20, 0] [10.35618782043457] [20143]
[3763, 48636] [20, 0] [10.35618782043457] [52399]
[19923, 34587] [20, 0] [10.35618782043457] [54510]
[4403, 59270] [20, 0] [10.35618782043457] [63673]
[57391, 17028] [12, 0] [10.416776657104492] [74419]
[76062, 10748] [12, 0] [10.416776657104492] [86810]
[14658, 59000] [20, 0] [10.35618782043457] [73658]
[83416, 2973] [20, 0] [10.35618782043457] [86389]
[812, 1289] [20, 0] [10.35618782043457] [2101]
[37900, 30036] [20, 0] [10.35618782043457] [67936]
[1370, 84528] [12, 0] [10.416776657104492

[68, 29] [13, 0] [9.91037368774414] [97]
[86, 2] [13, 0] [9.91037368774414] [88]
[59, 20] [13, 0] [9.91037368774414] [79]
[35, 40] [13, 0] [9.91037368774414] [75]
[28, 57] [13, 0] [9.91037368774414] [85]
[31, 31] [13, 0] [9.91037368774414] [62]
[40, 41] [13, 0] [9.91037368774414] [81]
[60, 15] [13, 0] [9.91037368774414] [75]
[21, 47] [13, 0] [9.91037368774414] [68]
[57, 11] [13, 0] [9.91037368774414] [68]
[36, 15] [13, 0] [9.91037368774414] [51]
[20, 63] [13, 0] [9.91037368774414] [83]
[64, 11] [13, 0] [9.91037368774414] [75]
[25, 42] [13, 0] [9.91037368774414] [67]
[33, 31] [13, 0] [9.91037368774414] [64]
[19, 46] [13, 0] [9.91037368774414] [65]
[25, 43] [13, 0] [9.91037368774414] [68]
[67, 28] [13, 0] [9.91037368774414] [95]
[74, 17] [13, 0] [9.91037368774414] [91]
[13, 50] [13, 0] [9.91037368774414] [63]
[13, 85] [13, 0] [9.91037368774414] [98]
[33, 22] [13, 0] [9.91037368774414] [55]
[6, 45] [13, 0] [9.91037368774414] [51]
[48, 22] [13, 0] [9.91037368774414] [70]
[17, 34] [13, 0] [

[37973, 51864] [62, 0] [9.657349586486816] [89837]
[33410, 506] [28, 0] [9.666330337524414] [33916]
[14334, 14175] [24, 0] [9.531519889831543] [28509]
[15419, 10763] [62, 0] [9.657349586486816] [26182]
[18634, 81031] [48, 0] [9.627931594848633] [99665]
[7295, 58273] [7, 0] [9.01294994354248] [65568]
[32645, 2599] [63, 0] [9.635356903076172] [35244]
[53774, 30503] [24, 0] [9.531519889831543] [84277]
[72163, 14971] [62, 0] [9.657349586486816] [87134]
[33317, 1080] [48, 0] [9.627931594848633] [34397]
[1378, 10344] [40, 0] [9.67034912109375] [11722]
[34060, 49109] [7, 0] [9.01294994354248] [83169]
[41271, 13826] [62, 0] [9.657349586486816] [55097]
[6760, 3895] [62, 0] [9.657349586486816] [10655]
[5925, 29303] [48, 0] [9.627931594848633] [35228]
[13062, 7081] [62, 0] [9.657349586486816] [20143]
[3763, 48636] [62, 0] [9.657349586486816] [52399]
[19923, 34587] [28, 0] [9.666330337524414] [54510]
[4403, 59270] [28, 0] [9.666330337524414] [63673]
[57391, 17028] [63, 0] [9.635356903076172] [7441

[55253, 4826] [36, 0] [9.380593299865723] [60079]
[51605, 40520] [4, 0] [9.048174858093262] [92125]
[8103, 29265] [41, 0] [9.432068824768066] [37368]
[30136, 24833] [18, 0] [9.44249439239502] [54969]
[651, 3815] [18, 0] [9.44249439239502] [4466]
[3220, 83] [18, 0] [9.44249439239502] [3303]
[10084, 19682] [41, 0] [9.432068824768066] [29766]
[2601, 4652] [2, 0] [9.254054069519043] [7253]
[48434, 16939] [36, 0] [9.380593299865723] [65373]
[13487, 9668] [63, 0] [9.44913101196289] [23155]
[27090, 14693] [36, 0] [9.380593299865723] [41783]
[213, 63147] [25, 0] [9.428655624389648] [63360]
[33450, 20066] [5, 0] [9.418961524963379] [53516]
[32771, 24732] [36, 0] [9.380593299865723] [57503]
[4156, 22211] [25, 0] [9.428655624389648] [26367]
[25894, 13944] [36, 0] [9.380593299865723] [39838]
[775, 3372] [18, 0] [9.44249439239502] [4147]
[31119, 32203] [4, 0] [9.048174858093262] [63322]
[8891, 5265] [41, 0] [9.432068824768066] [14156]
[25259, 7299] [18, 0] [9.44249439239502] [32558]
[7438, 4184] [3

...

[37973, 51864] [36, 0] [10.077489852905273] [89837]
[33410, 506] [36, 0] [10.077489852905273] [33916]
[14334, 14175] [51, 0] [10.06498908996582] [28509]
[15419, 10763] [51, 0] [10.06498908996582] [26182]
[18634, 81031] [36, 0] [10.077489852905273] [99665]
[7295, 58273] [51, 0] [10.06498908996582] [65568]
[32645, 2599] [2, 0] [10.063273429870605] [35244]
[53774, 30503] [51, 0] [10.06498908996582] [84277]
[72163, 14971] [51, 0] [10.06498908996582] [87134]
[33317, 1080] [36, 0] [10.077489852905273] [34397]
[1378, 10344] [2, 0] [10.063273429870605] [11722]
[34060, 49109] [26, 0] [10.157172203063965] [83169]
[41271, 13826] [51, 0] [10.06498908996582] [55097]
[6760, 3895] [23, 0] [10.065418243408203] [10655]
[5925, 29303] [51, 0] [10.06498908996582] [35228]
[13062, 7081] [25, 0] [10.066165924072266] [20143]
[3763, 48636] [25, 0] [10.066165924072266] [52399]
[19923, 34587] [25, 0] [10.066165924072266] [54510]
[4403, 59270] [26, 0] [10.157172203063965] [63673]
[57391, 17028] [51, 0] [10.064989

[37973, 51864] [18, 54, 0] [10.034571647644043] [89837]
[33410, 506] [53, 6, 0] [10.018661499023438] [33916]
[14334, 14175] [15, 10, 0] [10.021194458007812] [28509]
[15419, 10763] [10, 16, 0] [10.030874252319336] [26182]
[18634, 81031] [43, 16, 0] [10.035560607910156] [99665]
[7295, 58273] [20, 6, 0] [10.022174835205078] [65568]
[32645, 2599] [12, 10, 0] [10.029937744140625] [35244]
[53774, 30503] [60, 28, 0] [9.998785018920898] [84277]
[72163, 14971] [19, 10, 0] [10.01773738861084] [87134]
[33317, 1080] [35, 12, 0] [10.03125] [34397]
[1378, 10344] [2, 31, 0] [10.021127700805664] [11722]
[34060, 49109] [2, 3, 0] [10.030592918395996] [83169]
[41271, 13826] [44, 39, 0] [10.013648986816406] [55097]
[6760, 3895] [12, 31, 0] [10.019349098205566] [10655]
[5925, 29303] [49, 58, 0] [10.02851676940918] [35228]
[13062, 7081] [12, 43, 0] [10.041524887084961] [20143]
[3763, 48636] [12, 43, 0] [10.041524887084961] [52399]
[19923, 34587] [60, 10, 0] [10.016724586486816] [54510]
[4403, 59270] [18, 2,

[12, 2] [1, 6, 0] [9.720722198486328] [14]
[14, 0] [1, 5, 0] [9.70748233795166] [14]
[0, 20] [1, 5, 0] [9.70748233795166] [20]
[16, 3] [1, 14, 0] [9.719280242919922] [19]
[2, 18] [1, 6, 0] [9.720722198486328] [20]
[12, 7] [1, 5, 0] [9.70748233795166] [19]
[12, 8] [1, 2, 0] [9.64108657836914] [20]
[2, 13] [1, 13, 0] [9.716232299804688] [15]
[2, 11] [1, 14, 0] [9.719280242919922] [13]
[7, 9] [1, 13, 0] [9.716232299804688] [16]
[2, 12] [1, 9, 0] [9.68471908569336] [14]
[11, 4] [1, 14, 0] [9.719280242919922] [15]
[8, 9] [1, 15, 0] [9.71504020690918] [17]
[10, 10] [1, 5, 0] [9.70748233795166] [20]
[7, 11] [1, 6, 0] [9.720722198486328] [18]
[17, 2] [6, 6, 0] [9.680370330810547] [19]
[11, 2] [1, 9, 0] [9.68471908569336] [13]
[4, 13] [1, 14, 0] [9.719280242919922] [17]
[3, 11] [1, 13, 0] [9.716232299804688] [14]
[1, 19] [1, 5, 0] [9.70748233795166] [20]
[5, 14] [1, 1, 0] [9.723773002624512] [19]
[12, 1] [1, 5, 0] [9.70748233795166] [13]
[10, 8] [1, 15, 0] [9.71504020690918] [18]
[1, 14] [1, 14

[33224, 2385] [10, 61, 0] [9.064967155456543] [35609]
[15815, 62686] [45, 13, 0] [9.100850105285645] [78501]
[3574, 11698] [36, 19, 0] [9.068203926086426] [15272]
[40964, 901] [11, 19, 0] [9.074030876159668] [41865]
[25984, 52184] [45, 10, 0] [9.107752799987793] [78168]
[5819, 69981] [39, 25, 0] [9.066993713378906] [75800]
[9993, 39970] [48, 5, 0] [9.061326026916504] [49963]
[23378, 16009] [1, 16, 0] [9.103581428527832] [39387]
[951, 38740] [48, 36, 0] [9.088507652282715] [39691]
[5017, 66237] [39, 34, 0] [9.112561225891113] [71254]
[8657, 6456] [44, 6, 0] [9.066295623779297] [15113]
[6193, 6885] [41, 31, 0] [9.056211471557617] [13078]
[49718, 6025] [56, 34, 0] [9.104998588562012] [55743]
[11924, 5633] [16, 25, 0] [9.052674293518066] [17557]
[9725, 58929] [14, 31, 0] [9.075907707214355] [68654]
[45200, 34510] [16, 5, 0] [9.086892127990723] [79710]
[27809, 13646] [41, 56, 0] [9.082469940185547] [41455]
[20294, 23391] [5, 59, 0] [9.084502220153809] [43685]
[436, 15279] [54, 16, 0] [9.017

[30019, 41718] [1, 13, 0] [10.00329875946045] [71737]
[11591, 1840] [1, 6, 0] [10.015172958374023] [13431]
[624, 679] [1, 5, 0] [9.98427963256836] [1303]
[59491, 24438] [1, 15, 0] [10.00100040435791] [83929]
[38533, 54361] [13, 1, 0] [9.963836669921875] [92894]
[546, 18318] [1, 1, 0] [10.019258499145508] [18864]
[27239, 9845] [1, 15, 0] [10.00100040435791] [37084]
[10309, 9260] [6, 14, 0] [9.946118354797363] [19569]
[7956, 22462] [1, 13, 0] [10.00329875946045] [30418]
[49474, 2699] [1, 1, 0] [10.019258499145508] [52173]
[12717, 52228] [1, 1, 0] [10.019258499145508] [64945]
[76647, 10357] [14, 13, 0] [9.947772026062012] [87004]
[74912, 6153] [1, 6, 0] [10.015172958374023] [81065]
[20935, 18961] [1, 14, 0] [10.015324592590332] [39896]
[16754, 69529] [13, 1, 0] [9.963836669921875] [86283]
[29314, 58180] [1, 13, 0] [10.00329875946045] [87494]
[51480, 8427] [1, 12, 0] [9.977445602416992] [59907]
[3839, 17699] [1, 15, 0] [10.00100040435791] [21538]
[9618, 8223] [1, 1, 0] [10.019258499145508]

# Test various numbers

In [29]:
run_test(games10, lambda x: test_some_other_numbers(x))


--------
Running test for game 0
[9.0, 0.2] [7, 0] [9.499651908874512] [9.2]
[0.0, 0.3] [12, 0] [0.6291986703872681] [0.3]
[6.0, 4.0] [9, 0] [9.469077110290527] [10.0]
[6.0, 4.0] [3, 0] [9.498169898986816] [10.0]
[9.0, 1.0] [9, 0] [9.469077110290527] [10.0]
[9.0, 1.0] [11, 0] [9.48570728302002] [10.0]
[9.0, 1.0] [4, 0] [9.499030113220215] [10.0]
[1.0, 1.0] [2, 0] [2.596240520477295] [2.0]
[1.0, 1.0] [2, 0] [2.596240520477295] [2.0]
[1.0, 1.0] [2, 0] [2.596240520477295] [2.0]
[0.0, 1.0] [0, 0] [0.7613338232040405] [1.0]
[0.0, 0.0] [12, 0] [0.6291986703872681] [0.0]
[-1.0, 4.0] [2, 0] [2.596240520477295] [3.0]
[5.0, -2.0] [2, 0] [2.596240520477295] [3.0]
[-1.0, 0.0] [0, 0] [0.7613338232040405] [-1.0]
[-2.0, -2.0] [12, 0] [0.6291986703872681] [-4.0]
[-9.0, -1.0] [0, 0] [0.7613338232040405] [-10.0]
[8.0, -3.0] [15, 0] [4.493517875671387] [5.0]
[-10.0, -10.0] [12, 0] [0.6291986703872681] [-20.0]
Unique outputs: 9: {0.6291986703872681, 0.7613338232040405, 2.596240520477295, 4.49351787567138

# Test synonymy

In [30]:
number_range = 10
repeat_times = 100
run_test(games10, lambda x: test_synonymy(x, 10, 100))


--------
Running test for game 0
[0, 0] [12, 0] [0.6291986703872681] [0]
[0, 0] [12, 0] [0.6291986703872681] [0]
[0, 0] [0, 0] [0.7613338232040405] [0]
[0, 0] [0, 0] [0.7613338232040405] [0]
[0, 0] [12, 0] [0.6291986703872681] [0]
[0, 0] [12, 0] [0.6291986703872681] [0]
[0, 0] [12, 0] [0.6291986703872681] [0]
[0, 0] [0, 0] [0.7613338232040405] [0]
[0, 0] [12, 0] [0.6291986703872681] [0]
[0, 0] [0, 0] [0.7613338232040405] [0]
[0, 0] [12, 0] [0.6291986703872681] [0]
[0, 0] [12, 0] [0.6291986703872681] [0]
[0, 0] [12, 0] [0.6291986703872681] [0]
[0, 0] [0, 0] [0.7613338232040405] [0]
[0, 0] [12, 0] [0.6291986703872681] [0]
[0, 0] [0, 0] [0.7613338232040405] [0]
[0, 0] [12, 0] [0.6291986703872681] [0]
[0, 0] [12, 0] [0.6291986703872681] [0]
[0, 0] [0, 0] [0.7613338232040405] [0]
[0, 0] [12, 0] [0.6291986703872681] [0]
[0, 0] [0, 0] [0.7613338232040405] [0]
[0, 0] [12, 0] [0.6291986703872681] [0]
[0, 0] [0, 0] [0.7613338232040405] [0]
[0, 0] [12, 0] [0.6291986703872681] [0]
[0, 0] [0, 0] [

[0, 4] [15, 0] [4.493517875671387] [4]
[0, 4] [15, 0] [4.493517875671387] [4]
[0, 4] [15, 0] [4.493517875671387] [4]
[0, 4] [15, 0] [4.493517875671387] [4]
[0, 4] [15, 0] [4.493517875671387] [4]
[0, 4] [15, 0] [4.493517875671387] [4]
[0, 4] [15, 0] [4.493517875671387] [4]
[0, 4] [15, 0] [4.493517875671387] [4]
[0, 4] [15, 0] [4.493517875671387] [4]
[0, 4] [15, 0] [4.493517875671387] [4]
[0, 4] [15, 0] [4.493517875671387] [4]
[0, 4] [15, 0] [4.493517875671387] [4]
[0, 4] [15, 0] [4.493517875671387] [4]
[0, 4] [15, 0] [4.493517875671387] [4]
[0, 4] [15, 0] [4.493517875671387] [4]
[0, 4] [15, 0] [4.493517875671387] [4]
[0, 4] [15, 0] [4.493517875671387] [4]
[0, 4] [15, 0] [4.493517875671387] [4]
[0, 4] [15, 0] [4.493517875671387] [4]
[0, 4] [15, 0] [4.493517875671387] [4]
[0, 4] [15, 0] [4.493517875671387] [4]
[0, 4] [15, 0] [4.493517875671387] [4]
[0, 4] [15, 0] [4.493517875671387] [4]
[0, 4] [15, 0] [4.493517875671387] [4]
[0, 4] [15, 0] [4.493517875671387] [4]
[0, 4] [15, 0] [4.4935178

[1, 2] [2, 0] [2.596240520477295] [3]
[1, 2] [2, 0] [2.596240520477295] [3]
[1, 2] [2, 0] [2.596240520477295] [3]
[1, 2] [2, 0] [2.596240520477295] [3]
[1, 2] [2, 0] [2.596240520477295] [3]
[1, 2] [2, 0] [2.596240520477295] [3]
[1, 2] [2, 0] [2.596240520477295] [3]
[1, 2] [12, 0] [0.6291986703872681] [3]
[1, 2] [2, 0] [2.596240520477295] [3]
[1, 2] [2, 0] [2.596240520477295] [3]
[1, 2] [2, 0] [2.596240520477295] [3]
[1, 2] [2, 0] [2.596240520477295] [3]
[1, 2] [2, 0] [2.596240520477295] [3]
[1, 2] [2, 0] [2.596240520477295] [3]
[1, 2] [2, 0] [2.596240520477295] [3]
[1, 2] [2, 0] [2.596240520477295] [3]
[1, 2] [2, 0] [2.596240520477295] [3]
[1, 2] [2, 0] [2.596240520477295] [3]
[1, 2] [2, 0] [2.596240520477295] [3]
[1, 2] [2, 0] [2.596240520477295] [3]
[1, 2] [2, 0] [2.596240520477295] [3]
[1, 2] [2, 0] [2.596240520477295] [3]
[1, 2] [2, 0] [2.596240520477295] [3]
[1, 2] [2, 0] [2.596240520477295] [3]
[1, 2] [2, 0] [2.596240520477295] [3]
[1, 2] [2, 0] [2.596240520477295] [3]
[1, 2] [2,

[1, 5] [13, 0] [5.9797797203063965] [6]
[1, 5] [13, 0] [5.9797797203063965] [6]
[1, 5] [13, 0] [5.9797797203063965] [6]
[1, 5] [13, 0] [5.9797797203063965] [6]
[1, 5] [13, 0] [5.9797797203063965] [6]
[1, 5] [13, 0] [5.9797797203063965] [6]
[1, 5] [13, 0] [5.9797797203063965] [6]
[1, 5] [13, 0] [5.9797797203063965] [6]
[1, 5] [13, 0] [5.9797797203063965] [6]
[1, 5] [13, 0] [5.9797797203063965] [6]
[1, 5] [13, 0] [5.9797797203063965] [6]
[1, 5] [13, 0] [5.9797797203063965] [6]
[1, 5] [13, 0] [5.9797797203063965] [6]
[1, 5] [13, 0] [5.9797797203063965] [6]
[1, 5] [13, 0] [5.9797797203063965] [6]
[1, 5] [13, 0] [5.9797797203063965] [6]
[1, 5] [13, 0] [5.9797797203063965] [6]
[1, 5] [13, 0] [5.9797797203063965] [6]
[1, 5] [13, 0] [5.9797797203063965] [6]
[1, 5] [13, 0] [5.9797797203063965] [6]
[1, 5] [13, 0] [5.9797797203063965] [6]
[1, 5] [13, 0] [5.9797797203063965] [6]
[1, 5] [13, 0] [5.9797797203063965] [6]
[1, 5] [13, 0] [5.9797797203063965] [6]
[1, 5] [13, 0] [5.9797797203063965] [6]


[2, 5] [8, 0] [7.010116100311279] [7]
[2, 5] [8, 0] [7.010116100311279] [7]
[2, 5] [8, 0] [7.010116100311279] [7]
[2, 5] [8, 0] [7.010116100311279] [7]
[2, 5] [8, 0] [7.010116100311279] [7]
[2, 5] [8, 0] [7.010116100311279] [7]
[2, 5] [8, 0] [7.010116100311279] [7]
[2, 5] [8, 0] [7.010116100311279] [7]
[2, 5] [8, 0] [7.010116100311279] [7]
[2, 5] [8, 0] [7.010116100311279] [7]
[2, 5] [8, 0] [7.010116100311279] [7]
[2, 5] [8, 0] [7.010116100311279] [7]
[2, 5] [8, 0] [7.010116100311279] [7]
[2, 5] [8, 0] [7.010116100311279] [7]
[2, 5] [8, 0] [7.010116100311279] [7]
[2, 5] [8, 0] [7.010116100311279] [7]
[2, 5] [8, 0] [7.010116100311279] [7]
[2, 5] [8, 0] [7.010116100311279] [7]
[2, 5] [8, 0] [7.010116100311279] [7]
[2, 5] [8, 0] [7.010116100311279] [7]
[2, 5] [8, 0] [7.010116100311279] [7]
[2, 5] [8, 0] [7.010116100311279] [7]
[2, 5] [8, 0] [7.010116100311279] [7]
[2, 5] [8, 0] [7.010116100311279] [7]
[2, 5] [8, 0] [7.010116100311279] [7]
[2, 5] [8, 0] [7.010116100311279] [7]
[2, 5] [8, 0

...

[2, 1] [3, 6, 0] [2.9576544761657715] [3]
[2, 1] [4, 7, 0] [2.9482388496398926] [3]
[2, 1] [3, 6, 0] [2.9576544761657715] [3]
[2, 1] [7, 0, 0] [2.9879257678985596] [3]
[2, 1] [7, 4, 0] [2.9562883377075195] [3]
[2, 1] [4, 7, 0] [2.9482388496398926] [3]
[2, 1] [7, 0, 0] [2.9879257678985596] [3]
[2, 1] [10, 4, 0] [2.96063494682312] [3]
[2, 1] [4, 4, 0] [2.951491355895996] [3]
[2, 1] [7, 7, 0] [2.952695369720459] [3]
[2, 1] [10, 0, 0] [3.0123307704925537] [3]
[2, 1] [3, 13, 0] [2.928682327270508] [3]
[2, 1] [4, 7, 0] [2.9482388496398926] [3]
[2, 1] [7, 0, 0] [2.9879257678985596] [3]
[2, 1] [4, 4, 0] [2.951491355895996] [3]
[2, 1] [4, 7, 0] [2.9482388496398926] [3]
[2, 1] [3, 14, 0] [2.9555163383483887] [3]
[2, 1] [3, 6, 0] [2.9576544761657715] [3]
[2, 1] [7, 4, 0] [2.9562883377075195] [3]
[2, 1] [7, 4, 0] [2.9562883377075195] [3]
[2, 1] [4, 7, 0] [2.9482388496398926] [3]
[2, 1] [10, 4, 0] [2.96063494682312] [3]
[2, 1] [3, 15, 0] [2.9284956455230713] [3]
[2, 1] [10, 4, 0] [2.96063494682312]

[3, 4] [15, 4, 0] [7.034570217132568] [7]
[3, 4] [12, 2, 0] [6.868316650390625] [7]
[3, 4] [8, 2, 0] [6.881187438964844] [7]
[3, 4] [6, 3, 0] [6.769728183746338] [7]
[3, 4] [12, 8, 0] [7.017550945281982] [7]
[3, 4] [11, 12, 0] [6.991581916809082] [7]
[3, 4] [12, 11, 0] [7.006880283355713] [7]
[3, 4] [8, 8, 0] [7.030568599700928] [7]
[3, 4] [5, 12, 0] [6.9988813400268555] [7]
[3, 4] [11, 12, 0] [6.991581916809082] [7]
[3, 4] [13, 10, 0] [6.931556224822998] [7]
[3, 4] [15, 7, 0] [7.0089850425720215] [7]
[3, 4] [9, 2, 0] [6.858895301818848] [7]
[3, 4] [5, 2, 0] [6.882930278778076] [7]
[3, 4] [9, 8, 0] [7.010342597961426] [7]
[3, 4] [15, 4, 0] [7.034570217132568] [7]
[3, 4] [14, 3, 0] [6.748401165008545] [7]
[3, 4] [2, 13, 0] [6.962029933929443] [7]
[3, 4] [12, 8, 0] [7.017550945281982] [7]
[3, 4] [13, 7, 0] [6.958274841308594] [7]
[3, 4] [13, 7, 0] [6.958274841308594] [7]
[3, 4] [2, 15, 0] [6.924142837524414] [7]
[3, 4] [5, 8, 0] [7.028099060058594] [7]
[3, 4] [2, 6, 0] [7.033898830413818

[4, 4] [8, 14, 0] [8.002138137817383] [8]
[4, 4] [11, 13, 0] [8.006102561950684] [8]
[4, 4] [9, 6, 0] [7.998767375946045] [8]
[4, 4] [12, 14, 0] [7.9981794357299805] [8]
[4, 4] [5, 6, 0] [8.002490043640137] [8]
[4, 4] [1, 3, 0] [8.058520317077637] [8]
[4, 4] [5, 6, 0] [8.002490043640137] [8]
[4, 4] [9, 14, 0] [7.99683952331543] [8]
[4, 4] [9, 13, 0] [8.000433921813965] [8]
[4, 4] [5, 14, 0] [8.000231742858887] [8]
[4, 4] [5, 15, 0] [7.995031833648682] [8]
[4, 4] [8, 13, 0] [8.018787384033203] [8]
[4, 4] [5, 13, 0] [8.011055946350098] [8]
[4, 4] [11, 6, 0] [8.0016450881958] [8]
[4, 4] [8, 14, 0] [8.002138137817383] [8]
[4, 4] [14, 0, 0] [7.963180065155029] [8]
[4, 4] [9, 15, 0] [7.98643684387207] [8]
[4, 4] [13, 8, 0] [7.947038173675537] [8]
[4, 4] [14, 7, 0] [7.916849613189697] [8]
[4, 4] [9, 13, 0] [8.000433921813965] [8]
[4, 4] [5, 6, 0] [8.002490043640137] [8]
[4, 4] [15, 8, 0] [8.03941535949707] [8]
[4, 4] [5, 13, 0] [8.011055946350098] [8]
[4, 4] [15, 8, 0] [8.03941535949707] [8]


[6, 0] [13, 3, 0] [5.9299845695495605] [6]
[6, 0] [11, 0, 0] [5.999546051025391] [6]
[6, 0] [8, 0, 0] [5.996064186096191] [6]
[6, 0] [2, 8, 0] [5.898519515991211] [6]
[6, 0] [15, 3, 0] [5.950769901275635] [6]
[6, 0] [13, 3, 0] [5.9299845695495605] [6]
[6, 0] [9, 7, 0] [5.95353364944458] [6]
[6, 0] [8, 10, 0] [5.963550090789795] [6]
[6, 0] [8, 0, 0] [5.996064186096191] [6]
[6, 0] [13, 3, 0] [5.9299845695495605] [6]
[6, 0] [9, 7, 0] [5.95353364944458] [6]
[6, 0] [5, 4, 0] [5.973379611968994] [6]
[6, 0] [5, 10, 0] [5.948007583618164] [6]
[6, 0] [12, 4, 0] [5.960693836212158] [6]
[6, 0] [2, 12, 0] [5.878232479095459] [6]
[6, 0] [12, 10, 0] [5.945342063903809] [6]
[6, 0] [9, 4, 0] [5.956234455108643] [6]
[6, 0] [5, 0, 0] [6.006002902984619] [6]
[6, 0] [8, 7, 0] [5.966330528259277] [6]
[6, 0] [13, 3, 0] [5.9299845695495605] [6]
[6, 0] [9, 10, 0] [5.94058084487915] [6]
[6, 0] [15, 3, 0] [5.950769901275635] [6]
[6, 0] [8, 7, 0] [5.966330528259277] [6]
[6, 0] [13, 3, 0] [5.9299845695495605] [6]

[8, 1] [5, 1, 0] [9.022344589233398] [9]
[8, 1] [15, 15, 0] [9.073634147644043] [9]
[8, 1] [6, 9, 0] [9.0099515914917] [9]
[8, 1] [8, 1, 0] [9.029267311096191] [9]
[8, 1] [14, 12, 0] [9.007150650024414] [9]
[8, 1] [9, 1, 0] [9.017640113830566] [9]
[8, 1] [8, 1, 0] [9.029267311096191] [9]
[8, 1] [1, 0, 0] [8.81640338897705] [9]
[8, 1] [15, 6, 0] [9.011028289794922] [9]
[8, 1] [13, 13, 0] [8.985872268676758] [9]
[8, 1] [13, 15, 0] [8.998806953430176] [9]
[8, 1] [15, 15, 0] [9.073634147644043] [9]
[8, 1] [13, 6, 0] [8.973380088806152] [9]
[8, 1] [9, 1, 0] [9.017640113830566] [9]
[8, 1] [13, 6, 0] [8.973380088806152] [9]
[8, 1] [14, 9, 0] [9.003748893737793] [9]
[8, 1] [6, 12, 0] [9.013802528381348] [9]
[8, 1] [15, 13, 0] [9.053956031799316] [9]
[8, 1] [13, 14, 0] [8.955965042114258] [9]
[8, 1] [14, 8, 0] [9.013528823852539] [9]
[8, 1] [11, 1, 0] [9.020092010498047] [9]
[8, 1] [5, 1, 0] [9.022344589233398] [9]
[8, 1] [14, 9, 0] [9.003748893737793] [9]
[8, 1] [1, 4, 0] [8.968002319335938] [

In [31]:
def load_run(epochs, last_save, model_size, model_number, run_number, vocab, sender, receiver, embedding, length=1):
    epochs = epochs
    save_name = "game/models/game{}_{}_{}_{}_{}_{}_{}".format(model_size, model_number, run_number, vocab, sender, receiver, embedding)
    if(length > 1):
        save_name = "{}_{}".format(save_name, length)
    

    params = [
        '--batch_size=1',
        '--n_epochs={}'.format(epochs),
        '--vocab_size={}'.format(vocab),
        '--sender_hidden={}'.format(sender),
        '--receiver_hidden={}'.format(receiver),
        '--lr=0.001',
        '--max_len={}'.format(length),
        '--sender_entropy=0.5',
        '--sender_embedding={}'.format(embedding),
        '--receiver_embedding={}'.format(embedding),
        '--validation_freq=10',
        '--train_data=game/data/train10.txt',
        '--validation_data=game/data/validation10.txt',
        '--load_from_checkpoint={}_{}.tar'.format("game/models/game10_13_1_128", last_save)
    ]
    game = Game(params)
    game.play()
    game10_1.save_checkpoint(epochs, save_name)
    return game